# echuu v2 - AI VTuber 直播引擎（带完整剧本+记忆系统）

## 核心架构

```
标注数据 → Pattern Analyzer
               ↓
用户输入 (角色设定 + 话题)
               ↓
┌──────────────────────────────────────────────────────┐
│  Phase 1: 预生成完整剧本 (100s)                       │
│  • 10-15句完整台词，有起承转合                        │
│  • 每句标注 key_info（关键信息点）                   │
│  • 设置 interruption_cost                            │
└──────────────────────────────────────────────────────┘
               ↓
┌──────────────────────────────────────────────────────┐
│  Phase 2: 实时表演 + 记忆系统                         │
│                                                       │
│  🧠 记忆系统                                          │
│  ├─ 剧本进度（说到第几句）                            │
│  ├─ 已提到信息（避免重复）                            │
│  ├─ 弹幕记忆（已回应/待回答）                         │
│  └─ 承诺追踪（说了"等会告诉你"要兑现）                │
│                                                       │
│  ⚡ 统一弹幕处理                                      │
│  priority = base + relevance_bonus + sc_bonus        │
│  • 相关性是最重要因素                                 │
│  • 高相关问题 > 低相关SC                              │
│                                                       │
│  🔍 答案查找机制                                      │
│  在 key_info 中匹配问题 → 决定叙事策略                │
│  • 答案还没说：吊胃口 + 记录承诺                      │
│  • 答案在1-3句后：可跳跃（高优先级）                  │
│  • 答案已说过：提醒观众                               │
└──────────────────────────────────────────────────────┘
               ↓
     输出: 台词 + 🔊 语音 + 记忆状态可视化
```

## 核心创新

1. **完整剧本预生成** - 100s完整故事，避免车轱辘话
2. **key_info 标注** - 每句话的关键信息，用于匹配弹幕问题
3. **记忆系统** - 追踪已说内容、弹幕、承诺
4. **统一弹幕处理** - 相关性为王的优先级系统
5. **承诺追踪** - 说了"等会告诉你"必须兑现
6. **答案查找** - 在剧本中定位问题答案，决定叙事策略

In [111]:
# 💾 保存剧本（可选）
save_script_to_file(state_v2.script_lines, test_case_v2["name"], test_case_v2["topic"], scripts_dir)

# 📊 查看剧本进度
show_script_progress(state_v2)


NameError: name 'save_script_to_file' is not defined

## Part 1: 环境准备

In [104]:
# 安装依赖
!pip install anthropic dashscope python-dotenv -q


[notice] A new release of pip is available: 24.1.1 -> 25.3
[notice] To update, run: python.exe -m pip install --upgrade pip


In [ ]:
import json
import os
import sys
import re
import random
from pathlib import Path
from dataclasses import dataclass, field
from typing import List, Dict, Optional, Tuple, Callable
from enum import Enum
from collections import defaultdict, Counter
from datetime import datetime
import io

from IPython.display import display, HTML, Markdown, Audio

# 加载环境变量
from dotenv import load_dotenv

# 自动查找项目根目录
PROJECT_ROOT = Path.cwd()
while PROJECT_ROOT.name != 'echuu-agent' and PROJECT_ROOT.parent != PROJECT_ROOT:
    PROJECT_ROOT = PROJECT_ROOT.parent

load_dotenv(PROJECT_ROOT / '.env')

print(f"📁 项目根目录: {PROJECT_ROOT}")
print(f"🔑 ANTHROPIC_API_KEY: {'✅ 已配置' if os.getenv('ANTHROPIC_API_KEY') else '❌ 未配置'}")
print(f"🔑 DASHSCOPE_API_KEY: {'✅ 已配置' if os.getenv('DASHSCOPE_API_KEY') else '❌ 未配置'}")
print(f"\n✅ 导入完成（已添加 re, random 等V2所需模块）")

📁 项目根目录: D:\vtuberclip\echuu-agent
🔑 ANTHROPIC_API_KEY: ✅ 已配置
🔑 DASHSCOPE_API_KEY: ✅ 已配置

✅ 导入完成（已添加 re, random 等V2所需模块）


## Part 2: Pattern Analyzer - 从真实数据学习

In [106]:
class PatternAnalyzer:
    """从标注数据中提取模式"""
    
    def __init__(self, annotated_clips: List[Dict]):
        self.clips = annotated_clips
        self.all_segments = []
        for clip in annotated_clips:
            self.all_segments.extend(clip.get("segments", []))
    
    def _normalize_field(self, value, default="self"):
        """处理字段值，如果是列表则取第一个元素"""
        if isinstance(value, list):
            return value[0] if value else default
        return value if value else default
    
    def compute_attention_transitions(self) -> Dict[str, Dict[str, float]]:
        """计算attention转移概率"""
        trans = defaultdict(lambda: defaultdict(int))
        for clip in self.clips:
            segs = clip.get("segments", [])
            for i in range(len(segs) - 1):
                f = self._normalize_field(segs[i].get("attention_focus"), "self")
                t = self._normalize_field(segs[i+1].get("attention_focus"), "self")
                trans[f][t] += 1
        
        prob = {}
        for f, tos in trans.items():
            total = sum(tos.values())
            prob[f] = {t: c/total for t, c in tos.items()}
        return prob
    
    def infer_baseline_costs(self) -> Dict[str, float]:
        """推断不同attention下的打断代价"""
        focus_stats = defaultdict(lambda: {"total": 0, "ignored": 0})
        
        for seg in self.all_segments:
            focus = self._normalize_field(seg.get("attention_focus"), "self")
            trigger = self._normalize_field(seg.get("trigger"), "self")
            act = self._normalize_field(seg.get("speech_act"), "narrate")
            
            if trigger == "danmaku":
                focus_stats[focus]["total"] += 1
                if act != "respond":
                    focus_stats[focus]["ignored"] += 1
        
        costs = {}
        for focus, stats in focus_stats.items():
            if stats["total"] > 0:
                costs[focus] = stats["ignored"] / stats["total"]
            else:
                costs[focus] = 0.5
        return costs
    
    def extract_skeletons(self) -> List[Tuple[str, int]]:
        """提取叙事骨架"""
        skeletons = [c.get("skeleton", "") for c in self.clips if c.get("skeleton")]
        return Counter(skeletons).most_common(10)
    
    def extract_catchphrases(self, language: str = None) -> List[Tuple[str, int]]:
        """提取口癖"""
        cps = []
        for c in self.clips:
            if language and c.get("language") != language:
                continue
            cps.extend(c.get("catchphrases", []))
        return Counter(cps).most_common(20)
    
    def extract_hooks(self, language: str = None) -> List[str]:
        """提取开场示例"""
        hooks = []
        for c in self.clips:
            if language and c.get("language") != language:
                continue
            segs = c.get("segments", [])
            if segs:
                hooks.append(segs[0].get("text", "")[:100])
        return hooks[:10]
    
    def get_report(self) -> str:
        """生成分析报告"""
        lines = [
            "="*50,
            "📊 Pattern Analysis Report",
            "="*50,
            f"Total clips: {len(self.clips)}, Total segments: {len(self.all_segments)}",
        ]
        
        lines.append("\n### Attention Transitions")
        for f, tos in self.compute_attention_transitions().items():
            top = sorted(tos.items(), key=lambda x: -x[1])[:3]
            lines.append(f"- `{f}` → " + ", ".join(f"`{t}`:{p:.0%}" for t, p in top))
        
        lines.append("\n### Inferred Interruption Costs")
        for focus, cost in self.infer_baseline_costs().items():
            bar = "█" * int(cost * 10) + "░" * (10 - int(cost * 10))
            lines.append(f"- `{focus}`: {bar} {cost:.2f}")
        
        lines.append("\n### Top Catchphrases")
        cps = self.extract_catchphrases()[:10]
        lines.append(", ".join(f'"{c}"({n})' for c, n in cps))
        
        return "\n".join(lines)

## Part 3: 加载标注数据

In [107]:
# 加载标注数据
DATA_PATH = PROJECT_ROOT / "data" / "annotated_clips.json"

with open(DATA_PATH, "r", encoding="utf-8") as f:
    annotated_clips = json.load(f)

print(f"✅ 加载了 {len(annotated_clips)} 个clips")

# 创建分析器
analyzer = PatternAnalyzer(annotated_clips)

# 显示报告
display(Markdown(analyzer.get_report()))

✅ 加载了 30 个clips


==================================================
📊 Pattern Analysis Report
==================================================
Total clips: 30, Total segments: 101

### Attention Transitions
- `specific` → `self`:58%, `specific`:25%, `audience`:17%
- `audience` → `audience`:40%, `self`:40%, `specific`:13%
- `self` → `self`:59%, `audience`:27%, `content`:7%
- `content` → `self`:33%, `content`:33%, `audience`:33%

### Inferred Interruption Costs
- `self`: ██████████ 1.00
- `audience`: ███░░░░░░░ 0.33
- `specific`: ██░░░░░░░░ 0.20

### Top Catchphrases
"you know"(13), "like"(11), "我觉得"(4), "对吧"(3), "you know what I mean"(3), "uhm"(3), "what the f***"(3), "对不对"(2), "我跟你们说"(2), "oh my god"(2)

In [108]:
# 查看示例数据
print("\n📝 开场 Hook 示例 (中文):")
for i, hook in enumerate(analyzer.extract_hooks("zh")[:3], 1):
    print(f"  {i}. {hook[:60]}...")

print("\n📝 叙事骨架示例:")
for skel, count in analyzer.extract_skeletons()[:5]:
    print(f"  [{count}次] {skel[:50]}...")


📝 开场 Hook 示例 (中文):
  1. 所以说你只能把这条路走完，这个就是很多时候我们会很畏首畏尾的一个原因，就是因为有这个沉没成本在这里。...
  2. 猫猫怎么了？你也想要上镜是不是，小猫猫？小猫猫你也想要上镜，那你上镜啊，小猫猫！你上镜我就给你准备上镜礼物。是陈子又冠名...
  3. 谢谢XX的SC，"也可以先从宝宝起名开始"。不行不行不行，给活物起名是我的第一线。有很多人啊，他做选择是什么，他就想赖别...

📝 叙事骨架示例:
  [1次] 共情→自我经历→对比→建议→升华...
  [1次] 互动→抱怨→对比（外面的猫）→感慨→收尾...
  [1次] 拒绝→心理分析（举例）→延伸（宠物/孩子）→总结...
  [1次] 吐槽→自我发现→担忧→自嘲→反转...
  [1次] 开场悬念→背景铺垫（穷）→核心故事（偷吃腰果）→高潮（坦白）→释放→收尾（广告）...


## Part 4: TTS Client - 通义千问语音合成

In [109]:
class TTSClient:
    """通义千问 CosyVoice TTS 客户端（增强版）"""
    
    # 📋 所有可用音色列表（从官方文档提取 2025-11-27）
    # 参考: https://help.aliyun.com/zh/model-studio/qwen-tts-realtime
    AVAILABLE_VOICES = [
        # ===== 🎀 可爱/萌系女声 =====
        "Cherry",           # 芊悦 - 阳光积极、亲切自然小姐姐
        "Serena",           # 苏瑶 - 温柔小姐姐
        "Chelsie",          # 千雪 - 二次元虚拟女友 ⭐推荐VTuber
        "Momo",             # 茉兔 - 撒娇搞怪，逗你开心 ⭐推荐VTuber
        "Vivian",           # 十三 - 拽拽的，可爱的小暴躁
        "Bunny",            # 萌小姬 - 萌属性爆棚的小萝莉 ⭐推荐VTuber
        "Bella",            # 萌宝 - 喝酒不打醉拳的小萝莉
        "Mia",              # 乖小妹 - 温顺如春水，乖巧如初雪
        "Stella",           # 少女阿月 - 甜到发腻的迷糊少女音
        "Nini",             # 声拉长了的'哥哥'，甜得骨头都酥了
        
        # ===== 👩 知性/成熟女声 =====
        "Katerina",         # 卡捷琳娜 - 御姐音色，韵律回味十足
        "Maia",             # 四月 - 知性与温柔的碰撞
        "Seren",            # 小婉 - 温和舒缓，助眠声线
        "Bellona",          # 燕铮莹 - 声音洪亮，吐字清晰，热血江湖
        "Elias",            # 墨讲师 - 学科严谨，叙事技巧
        "Jennifer",         # 詹妮弗 - 品牌级电影质感美语女声
        
        # ===== 👨 阳光/年轻男声 =====
        "Ethan",            # 晨煦 - 标准普通话，阳光温暖活力朝气
        "Ryan",             # 甜茶 - 节奏拉满，戏感炸裂
        "Aiden",            # 艾登 - 精通厨艺的美语大男孩
        "Moon",             # 月白 - 率性帅气
        "Kai",              # 凯 - 耳朵的一场SPA
        "Nofish",           # 不吃鱼 - 不会翘舌音的设计师
        
        # ===== 👴 成熟/磁性男声 =====
        "Andre",            # 安德雷 - 声音磁性，自然舒服沉稳
        "Vincent",          # 田叔 - 沙哑烟嗓，千军万马江湖豪情
        "Eldric_Sage",      # 沧明子 - 沉稳睿智老者，沧桑如松
        "Arthur",           # 徐大爷 - 质朴嗓音，满村奇闻异事
        "Neil",             # 阿闻 - 专业新闻主持人，字正腔圆
        
        # ===== 🌍 外语/方言特色 =====
        "Dolce",            # 多尔切 - 慵懒意大利大叔（男）
        "Sohee",            # 素熙 - 温柔开朗韩国欧尼（女）
        "Ono_Anna",         # 小野杏 - 鬼灵精怪青梅竹马（女，日系）
        "Lenn",             # 莱恩 - 叛逆德国青年（男）
        "Emilien",          # 埃米尔安 - 浪漫法国大哥哥（男）
        "Li",               # 南京老李 - 耐心瑜伽老师（男，南京话）
        "Marcus",           # 秦川 - 老陕味道（男，陕西话）
        "Roy",              # 阿杰 - 诙谐直爽台湾哥仔（男，闽南语）
        "Peter",            # 李彼得 - 天津相声捧哏（男，天津话）
        "Sunny",            # 晴儿 - 甜到心里的川妹子（女，四川话）
        "Eric",             # 程川 - 跳脱市井成都男子（男，四川话）
        
        # ===== 👶 儿童/特殊 =====
        "Mochi",            # 沙小弥 - 聪明伶俐小大人，童真早慧（男童）
        "Pip",              # 顽屁小孩 - 调皮捣蛋充满童真（男童）
        "Ebona",            # 诡婆婆 - 幽暗角落，童年阴影恐惧（特殊）
    ]
    
    # 🎯 VTuber推荐音色
    VTUBER_RECOMMENDED = ["Chelsie", "Momo", "Bunny", "Cherry", "Vivian", "Stella"]
    
    def __init__(self):
        self.enabled = False
        self.synthesizer_class = None
        self.audio_format = None
        
        # 情绪控制参数
        self.rate = 1.0      # 语速 0.5-2.0
        self.pitch = 0       # 音调 -500到500
        self.volume = 50     # 音量 0-100
        
        # 录制缓存
        self.recording_buffer = []
        
        api_key = os.getenv("DASHSCOPE_API_KEY")
        if api_key:
            try:
                import dashscope
                from dashscope.audio.tts_v2 import SpeechSynthesizer, AudioFormat
                
                dashscope.api_key = api_key
                self.synthesizer_class = SpeechSynthesizer
                self.audio_format = AudioFormat.MP3_22050HZ_MONO_256KBPS
                self.model = os.getenv("TTS_MODEL", "cosyvoice-v3-flash")
                self.voice = os.getenv("TTS_VOICE", "longanyang")
                self.enabled = True
                print(f"✅ TTS 已启用: model={self.model}, voice={self.voice}")
                print(f"   情绪参数: rate={self.rate}, pitch={self.pitch}, volume={self.volume}")
                print(f"   可用音色: {len(self.AVAILABLE_VOICES)} 个")
            except ImportError:
                print("⚠️ dashscope 未安装")
        else:
            print("⚠️ 未设置 DASHSCOPE_API_KEY，TTS 已禁用")
    
    def synthesize(self, text: str, emotion_boost: float = 0.0) -> Optional[bytes]:
        """
        合成语音，返回音频数据
        
        Args:
            text: 要合成的文本
            emotion_boost: 情绪增强系数 0.0-1.0
                          0.0 = 正常语速
                          1.0 = 最大情绪变化（语速±50%，音调±200）
        """
        if not self.enabled:
            return None
        
        try:
            # 根据 emotion_boost 动态调整参数
            dynamic_rate = self.rate
            dynamic_pitch = self.pitch
            
            if emotion_boost > 0:
                # 随机增强情绪变化
                import random
                rate_variance = 0.5 * emotion_boost  # 最大±50%语速
                pitch_variance = 200 * emotion_boost  # 最大±200音调
                
                dynamic_rate = self.rate * (1 + random.uniform(-rate_variance, rate_variance))
                dynamic_rate = max(0.5, min(2.0, dynamic_rate))  # 限制范围
                
                dynamic_pitch = self.pitch + random.randint(
                    int(-pitch_variance), 
                    int(pitch_variance)
                )
                dynamic_pitch = max(-500, min(500, dynamic_pitch))  # 限制范围
            
            synthesizer = self.synthesizer_class(
                model=self.model,
                voice=self.voice,
                format=self.audio_format
            )
            
            # 注意：阿里云 TTS API 的参数名可能有所不同，需要查看最新文档
            audio_data = synthesizer.call(
                text,
                sample_rate=22050,
                # rate=dynamic_rate,    # 如果API支持，取消注释
                # pitch=dynamic_pitch,  # 如果API支持，取消注释
                # volume=self.volume,   # 如果API支持，取消注释
            )
            
            # 添加到录制缓存
            if audio_data:
                self.recording_buffer.append(audio_data)
            
            return audio_data
        except Exception as e:
            print(f"[TTS] 错误: {e}")
            return None
    
    def change_voice(self, voice: str):
        """切换音色"""
        if voice in self.AVAILABLE_VOICES:
            self.voice = voice
            print(f"🔊 音色已切换为: {voice}")
        else:
            print(f"⚠️ 未知音色: {voice}")
            print(f"   可用音色: {', '.join(self.AVAILABLE_VOICES[:5])}...")
    
    def set_emotion_params(self, rate: float = None, pitch: int = None, volume: int = None):
        """设置情绪参数"""
        if rate is not None:
            self.rate = max(0.5, min(2.0, rate))
        if pitch is not None:
            self.pitch = max(-500, min(500, pitch))
        if volume is not None:
            self.volume = max(0, min(100, volume))
        print(f"🎛️ 情绪参数已更新: rate={self.rate}, pitch={self.pitch}, volume={self.volume}")
    
    def start_recording(self):
        """开始录制"""
        self.recording_buffer = []
        print("🔴 开始录制直播音频...")
    
    def save_recording(self, output_path: str):
        """保存录制的音频"""
        if not self.recording_buffer:
            print("⚠️ 没有可保存的音频")
            return
        
        try:
            from pydub import AudioSegment
            import io
            
            # 合并所有音频片段
            combined = AudioSegment.empty()
            for audio_data in self.recording_buffer:
                audio = AudioSegment.from_file(io.BytesIO(audio_data), format="mp3")
                combined += audio
            
            # 保存
            combined.export(output_path, format="mp3")
            print(f"💾 直播音频已保存到: {output_path}")
            print(f"   总时长: {len(combined)/1000:.1f}秒")
        except ImportError:
            print("⚠️ 需要安装 pydub: pip install pydub")
            # 简单保存：拼接原始数据（不推荐）
            with open(output_path, "wb") as f:
                for audio_data in self.recording_buffer:
                    f.write(audio_data)
            print(f"💾 音频已保存（未合并）: {output_path}")
        except Exception as e:
            print(f"❌ 保存失败: {e}")


# 初始化 TTS
tts = TTSClient()

✅ TTS 已启用: model=cosyvoice-v3-flash, voice=longanyang
   情绪参数: rate=1.0, pitch=0, volume=50
   可用音色: 41 个


In [110]:
# 🎤 TTS 测试和音色切换工具
if tts.enabled:
    print("🎤 测试 TTS...")
    test_audio = tts.synthesize("你好，我是echuu AI主播，今天来给大家讲个有趣的故事！")
    if test_audio:
        print(f"✅ 生成音频: {len(test_audio)} bytes")
        display(Audio(test_audio, autoplay=False))
    
    # 显示 VTuber 推荐音色
    print(f"\n⭐ VTuber 推荐音色:")
    for voice in tts.VTUBER_RECOMMENDED:
        print(f"  • {voice}")
    
    # 显示所有可用音色（按分类）
    print(f"\n🎨 所有可用音色 ({len(tts.AVAILABLE_VOICES)}个):")
    categories = {
        "🎀 萌系女声": ["Cherry", "Serena", "Chelsie", "Momo", "Vivian", "Bunny", "Bella", "Mia", "Stella", "Nini"],
        "👩 知性女声": ["Katerina", "Maia", "Seren", "Bellona", "Elias", "Jennifer"],
        "👨 阳光男声": ["Ethan", "Ryan", "Aiden", "Moon", "Kai", "Nofish"],
        "👴 磁性男声": ["Andre", "Vincent", "Eldric_Sage", "Arthur", "Neil"],
        "🌍 方言特色": ["Li", "Marcus", "Roy", "Peter", "Sunny", "Eric"],
        "🌐 外语": ["Dolce", "Sohee", "Ono_Anna", "Lenn", "Emilien"],
        "👶 儿童/特殊": ["Mochi", "Pip", "Ebona"],
    }
    for cat, voices in categories.items():
        print(f"  {cat}: {', '.join(voices)}")
    
    # 测试情绪增强
    print("\n🔥 测试情绪增强 (emotion_boost=0.8):")
    emotional_audio = tts.synthesize("天哪！你们是不是不相信？！真的超级好笑！", emotion_boost=0.8)
    if emotional_audio:
        print(f"✅ 情绪化音频: {len(emotional_audio)} bytes")
        display(Audio(emotional_audio, autoplay=False))
else:
    print("⚠️ TTS 未启用，跳过测试")

# 💡 快速切换音色的辅助函数
def test_voice(voice_name: str, text: str = "你好，我是六螺，这是我的声音测试。"):
    """快速测试某个音色"""
    if not tts.enabled:
        print("⚠️ TTS 未启用")
        return
    
    tts.change_voice(voice_name)
    audio = tts.synthesize(text)
    if audio:
        print(f"🔊 播放音色: {voice_name}")
        display(Audio(audio, autoplay=True))

print("\n💡 使用示例:")
print("   test_voice('Chelsie', '大家好呀~ 我是千雪！今天来讲个有趣的故事~')  # 二次元女友")
print("   test_voice('Momo', '喵~ 今天也要开心哦！')  # 撒娇搞怪")
print("   test_voice('Bunny', '萌萌哒~ 宝贝们好呀！')  # 萝莉音")
print("   test_voice('Ethan', '各位好，今天来给大家讲个故事')  # 阳光男声")

🎤 测试 TTS...
[TTS] 错误: SpeechSynthesizer.call() got an unexpected keyword argument 'sample_rate'

⭐ VTuber 推荐音色:
  • Chelsie
  • Momo
  • Bunny
  • Cherry
  • Vivian
  • Stella

🎨 所有可用音色 (41个):
  🎀 萌系女声: Cherry, Serena, Chelsie, Momo, Vivian, Bunny, Bella, Mia, Stella, Nini
  👩 知性女声: Katerina, Maia, Seren, Bellona, Elias, Jennifer
  👨 阳光男声: Ethan, Ryan, Aiden, Moon, Kai, Nofish
  👴 磁性男声: Andre, Vincent, Eldric_Sage, Arthur, Neil
  🌍 方言特色: Li, Marcus, Roy, Peter, Sunny, Eric
  🌐 外语: Dolce, Sohee, Ono_Anna, Lenn, Emilien
  👶 儿童/特殊: Mochi, Pip, Ebona

🔥 测试情绪增强 (emotion_boost=0.8):
[TTS] 错误: SpeechSynthesizer.call() got an unexpected keyword argument 'sample_rate'

💡 使用示例:
   test_voice('Chelsie', '大家好呀~ 我是千雪！今天来讲个有趣的故事~')  # 二次元女友
   test_voice('Momo', '喵~ 今天也要开心哦！')  # 撒娇搞怪
   test_voice('Bunny', '萌萌哒~ 宝贝们好呀！')  # 萝莉音
   test_voice('Ethan', '各位好，今天来给大家讲个故事')  # 阳光男声


## Part 5: LLM Client - Claude

In [96]:
class LLMClient:
    """Claude LLM 客户端"""
    
    def __init__(self):
        self.client = None
        self.model = os.getenv("claude-sonnet-4-20250514", "claude-sonnet-4-20250514")
        
        api_key = os.getenv("ANTHROPIC_API_KEY")
        if api_key:
            try:
                import anthropic
                self.client = anthropic.Anthropic(api_key=api_key)
                print(f"✅ LLM 已初始化: {self.model}")
            except ImportError:
                print("⚠️ anthropic 未安装")
        else:
            print("⚠️ 未设置 ANTHROPIC_API_KEY，使用 Mock 模式")
    
    def call(self, prompt: str, system: str = None, max_tokens: int = 1000) -> str:
        """调用 LLM"""
        if self.client:
            try:
                kwargs = {
                    "model": self.model,
                    "max_tokens": max_tokens,
                    "messages": [{"role": "user", "content": prompt}]
                }
                if system:
                    kwargs["system"] = system
                
                response = self.client.messages.create(**kwargs)
                return response.content[0].text
            except Exception as e:
                print(f"[LLM] 错误: {e}")
        
        return self._mock_response(prompt)
    
    def _mock_response(self, prompt: str) -> str:
        """Mock 响应"""
        import random
        
        if "JSON数组" in prompt or "script" in prompt.lower():
            return '''[
{"stage": "Hook", "goal": "用悬念开场", "attention": "audience", "speech_act": "elicit", "duration": 20, "cost": 0.3, "hint": "提问开场"},
{"stage": "Build-up", "goal": "铺垫背景", "attention": "self", "speech_act": "narrate", "duration": 40, "cost": 0.6, "hint": "描述情况"},
{"stage": "Climax", "goal": "关键转折", "attention": "self", "speech_act": "narrate", "duration": 40, "cost": 0.9, "hint": "情感爆发"},
{"stage": "Resolution", "goal": "总结感悟", "attention": "audience", "speech_act": "opine", "duration": 20, "cost": 0.4, "hint": "分享心得"}
]'''
        else:
            return json.dumps({
                "inner_monologue": random.choice(["让我想想...", "有意思...", "继续...", "嗯..."]),
                "decision": "continue",
                "speech": random.choice(["说起这个事儿啊...", "你们知道吗...", "我跟你们讲..."]),
                "emotion": "neutral"
            }, ensure_ascii=False)


# 初始化 LLM
llm = LLMClient()

✅ LLM 已初始化: claude-sonnet-4-20250514


## Part 6: 数据结构定义

In [ ]:
# 🔥 SC响应优化：提高SC优先级，确保主播积极响应

# 重写 DanmakuEvaluator.evaluate 方法，提高SC加成
original_evaluate = DanmakuEvaluator.evaluate

def enhanced_evaluate(self, danmaku: Danmaku, state: PerformanceState) -> Danmaku:
    """增强版评估：大幅提高SC优先级"""
    # 调用原始评估
    danmaku = original_evaluate(self, danmaku, state)
    
    # 🔥 SC特权增强
    if danmaku.is_sc:
        # 重新计算SC加成（更高的值）
        if danmaku.amount >= 200:
            sc_bonus_extra = 0.3  # 从0.7提升到1.0
        elif danmaku.amount >= 100:
            sc_bonus_extra = 0.3  # 从0.5提升到0.8
        elif danmaku.amount >= 50:
            sc_bonus_extra = 0.3  # 从0.3提升到0.6
        else:
            sc_bonus_extra = 0.2  # 从0.2提升到0.4
        
        danmaku.priority += sc_bonus_extra
        
        # SC特权：低相关性也给保底bonus
        if danmaku.relevance < 0.3:
            danmaku.priority += 0.2  # 保底优先级
    
    return danmaku

# 应用增强
DanmakuEvaluator.evaluate = enhanced_evaluate

# 重新创建弹幕处理器
evaluator = DanmakuEvaluator()
danmaku_handler = DanmakuHandler(evaluator)

print("✅ SC响应已优化：")
print("   • ¥50 SC优先级提升至 ~1.1（可打断大部分阶段）")
print("   • ¥100+ SC优先级提升至 1.3+（可打断任何阶段）")
print("   • 低相关性SC也会获得保底优先级")
print("   • improvise模式已改为积极响应，不再说'与话题无关'")


In [97]:
# ==================== 核心数据结构 ====================

@dataclass
class ScriptLine:
    """剧本台词（带key_info标注）"""
    id: str                          # 唯一ID
    text: str                        # 台词内容
    stage: str                       # Hook/Build-up/Climax/Resolution
    interruption_cost: float         # 0.0-1.0
    key_info: List[str] = field(default_factory=list)  # 🔑 关键信息点（用于匹配弹幕）
    
    def __repr__(self):
        info_str = ", ".join(self.key_info[:2])
        return f"[{self.stage}] {self.text[:30]}... (keys: {info_str})"


@dataclass
class Danmaku:
    """弹幕（带优先级计算）"""
    text: str
    user: str = "观众"
    is_sc: bool = False
    amount: int = 0              # SC金额
    
    # 计算得出的属性
    relevance: float = 0.0       # 与当前话题的相关性 0.0-1.0
    priority: float = 0.0        # 最终优先级
    
    @classmethod
    def from_text(cls, text: str) -> "Danmaku":
        """解析弹幕"""
        is_sc = False
        amount = 0
        
        # 检测SC
        if "SC" in text or "¥" in text or "$" in text:
            is_sc = True
            # 简单提取金额
            import re
            match = re.search(r'[¥$]?\s*(\d+)', text)
            if match:
                amount = int(match.group(1))
        
        return cls(text=text, is_sc=is_sc, amount=amount)
    
    def is_question(self) -> bool:
        """判断是否是问题"""
        return "?" in self.text or "？" in self.text


@dataclass
class PerformerMemory:
    """
    记忆系统 - 可视化展示AI记住了什么
    """
    
    # 📖 剧本进度
    script_progress: Dict = field(default_factory=lambda: {
        "current_line": 0,
        "total_lines": 0,
        "completed_stages": [],
        "current_stage": "Hook",
    })
    
    # 💬 弹幕记忆
    danmaku_memory: Dict = field(default_factory=lambda: {
        "received": [],          # 收到的所有弹幕
        "responded": [],         # 已回应的
        "ignored": [],           # 被忽略的
        "pending_questions": [], # 待回答的问题
    })
    
    # 🤝 承诺追踪
    promises: List[Dict] = field(default_factory=list)
    # 例如: {"content": "室友生不生气", "made_at_step": 3, "fulfilled": False, "answer_at_line": 9}
    
    # 🎭 故事要点
    story_points: Dict = field(default_factory=lambda: {
        "mentioned": [],         # 已经提到的信息
        "upcoming": [],          # 即将要说的关键点
        "revealed": [],          # 已揭示的"答案"
    })
    
    # 😊 情绪轨迹
    emotion_track: List[Dict] = field(default_factory=list)
    
    def to_display(self) -> str:
        """生成用户可见的记忆状态"""
        lines = []
        lines.append("┌─────────────────────────────────────────────┐")
        lines.append("│ 🧠 AI记忆状态                               │")
        lines.append("├─────────────────────────────────────────────┤")
        
        # 剧本进度
        prog = self.script_progress
        current = prog.get("current_line", 0)
        total = prog.get("total_lines", 0)
        if total > 0:
            percent = int(current / total * 10)
            bar = "█" * percent + "░" * (10 - percent)
            lines.append(f"│ 📖 剧本: [{bar}] {current}/{total} ({prog.get('current_stage', '?')})  │")
        
        # 弹幕记忆
        dm = self.danmaku_memory
        responded = len(dm.get("responded", []))
        pending = len(dm.get("pending_questions", []))
        lines.append(f"│ 💬 弹幕: 已回应{responded}条, 待回答{pending}个问题         │")
        
        # 承诺
        unfulfilled = [p for p in self.promises if not p.get("fulfilled", False)]
        if unfulfilled:
            lines.append("│ 🤝 待兑现承诺:                              │")
            for p in unfulfilled[:2]:
                content = p.get("content", "")[:20]
                lines.append(f"│    • {content}...                         │")
        
        # 已提到要点
        mentioned = self.story_points.get("mentioned", [])
        if mentioned:
            lines.append("│ 🎭 已提到:                                  │")
            for point in mentioned[-3:]:
                lines.append(f"│    ✓ {point[:20]}...                      │")
        
        lines.append("└─────────────────────────────────────────────┘")
        return "\n".join(lines)
    
    def to_context(self) -> str:
        """生成给LLM的上下文摘要"""
        parts = []
        
        # 剧本进度
        prog = self.script_progress
        parts.append(f"剧本进度: {prog.get('current_line')}/{prog.get('total_lines')} ({prog.get('current_stage')})")
        
        # 已提到的信息
        mentioned = self.story_points.get("mentioned", [])
        if mentioned:
            parts.append(f"已提到: {', '.join(mentioned[-5:])}")
        
        # 待回答问题
        pending = self.danmaku_memory.get("pending_questions", [])
        if pending:
            parts.append(f"待回答: {', '.join(q[:20] for q in pending[:3])}")
        
        # 未兑现承诺
        unfulfilled = [p for p in self.promises if not p.get("fulfilled", False)]
        if unfulfilled:
            parts.append(f"待兑现承诺: {', '.join(p['content'][:15] for p in unfulfilled[:2])}")
        
        return " | ".join(parts)


@dataclass
class PerformanceState:
    """表演状态"""
    name: str
    persona: str
    background: str
    topic: str
    
    # 完整剧本（预生成）
    script_lines: List[ScriptLine] = field(default_factory=list)
    current_line_idx: int = 0
    current_step: int = 0
    
    # 记忆系统
    memory: PerformerMemory = field(default_factory=PerformerMemory)
    
    # 弹幕队列
    danmaku_queue: List[Danmaku] = field(default_factory=list)
    
    # 口癖
    catchphrases: List[str] = field(default_factory=list)

## Part 7: 弹幕处理核心（统一优先级系统）

In [98]:
# ==================== 工具函数 ====================

def extract_keywords(text: str) -> List[str]:
    """提取关键词（简单版）"""
    import re
    # 移除标点
    text = re.sub(r'[，。！？、：；""''（）【】《》…~]', ' ', text)
    # 分词（简单按空格）
    words = text.split()
    # 过滤停用词
    stopwords = {'的', '了', '在', '是', '我', '你', '他', '她', '它', '们', 
                 '这', '那', '有', '和', '就', '不', '也', '都', '说', '很',
                 '吗', '吧', '呢', '啊', '哦', '嗯', '哈', '呀'}
    keywords = [w for w in words if len(w) >= 2 and w not in stopwords]
    return keywords[:5]  # 最多5个


# ==================== 弹幕处理器 ====================

class DanmakuEvaluator:
    """
    弹幕评估器 - 计算优先级
    
    优先级公式:
    priority = base_score + relevance_bonus + sc_bonus
    """
    
    def evaluate(self, danmaku: Danmaku, state: PerformanceState) -> Danmaku:
        """评估单条弹幕"""
        
        # 1. 基础分
        if danmaku.is_question():
            base = 0.3  # 问题类
        elif any(kw in danmaku.text for kw in ["哈哈", "笑死", "真的假的", "！", "牛"]):
            base = 0.15  # 情绪反馈类
        else:
            base = 0.1  # 普通评论
        
        # 2. 相关性评估
        relevance = self._calc_relevance(danmaku.text, state)
        danmaku.relevance = relevance
        
        if relevance > 0.7:
            relevance_bonus = 0.4  # 高相关
        elif relevance > 0.4:
            relevance_bonus = 0.2  # 中相关
        else:
            relevance_bonus = 0.0  # 低相关
        
        # 3. SC加成
        if danmaku.is_sc:
            if danmaku.amount >= 200:
                sc_bonus = 0.7
            elif danmaku.amount >= 100:
                sc_bonus = 0.5
            elif danmaku.amount >= 50:
                sc_bonus = 0.3
            else:
                sc_bonus = 0.2
        else:
            sc_bonus = 0.0
        
        danmaku.priority = base + relevance_bonus + sc_bonus
        
        return danmaku
    
    def _calc_relevance(self, text: str, state: PerformanceState) -> float:
        """计算弹幕与当前上下文的相关性"""
        # 提取当前故事的关键词
        story_keywords = set()
        for info in state.memory.story_points.get("mentioned", []):
            story_keywords.update(extract_keywords(info))
        for info in state.memory.story_points.get("upcoming", []):
            story_keywords.update(extract_keywords(info))
        
        # 如果没有故事关键词，检查话题
        if not story_keywords:
            story_keywords.update(extract_keywords(state.topic))
        
        # 提取弹幕关键词
        danmaku_keywords = set(extract_keywords(text))
        
        # 计算重叠度
        if not story_keywords:
            return 0.0
        overlap = len(danmaku_keywords & story_keywords)
        return min(overlap / 2, 1.0)  # 2个关键词重叠就算高相关


class DanmakuHandler:
    """
    统一弹幕处理器
    
    所有弹幕走同一流程，根据优先级决定：
    1. 是否打断
    2. 是否复读
    3. 如何回应
    4. 是否改变叙事
    """
    
    def __init__(self, evaluator: DanmakuEvaluator):
        self.evaluator = evaluator
    
    def handle(self, danmaku: Danmaku, state: PerformanceState) -> Dict:
        """
        处理弹幕
        
        Returns:
            {
                "should_interrupt": bool,
                "echo": str,
                "response": str,
                "action": str,  # continue/jump/tease/improvise
            }
        """
        
        # 评估优先级
        danmaku = self.evaluator.evaluate(danmaku, state)
        
        # 获取当前cost
        if state.current_line_idx >= len(state.script_lines):
            current_cost = 0.2  # 结尾阶段
        else:
            current_line = state.script_lines[state.current_line_idx]
            current_cost = current_line.interruption_cost
        
        # 决策：是否打断
        should_interrupt = danmaku.priority > current_cost
        
        if not should_interrupt:
            return {
                "should_interrupt": False,
                "action": "ignore",
                "priority": danmaku.priority,
                "cost": current_cost
            }
        
        # 决定是否复读
        echo = self._maybe_echo(danmaku)
        
        # 查找答案位置
        answer_loc = self._find_answer(danmaku.text, state)
        
        # 生成回应策略
        action = self._decide_action(danmaku, answer_loc, state)
        
        return {
            "should_interrupt": True,
            "echo": echo,
            "action": action,
            "answer_loc": answer_loc,
            "priority": danmaku.priority,
            "cost": current_cost,
            "relevance": danmaku.relevance
        }
    
    def _maybe_echo(self, danmaku: Danmaku) -> str:
        """决定是否复读弹幕"""
        if danmaku.is_sc:
            return f"诶有SC！有人说：{danmaku.text}"
        elif danmaku.priority > 0.5:
            return f"有人说{danmaku.text}，"
        elif danmaku.is_question():
            return f"有人问{danmaku.text}，"
        else:
            return ""  # 不复读
    
    def _find_answer(self, question: str, state: PerformanceState) -> Dict:
        """在剧本中查找问题的答案位置"""
        keywords = extract_keywords(question)
        current_idx = state.current_line_idx
        
        for i, line in enumerate(state.script_lines):
            if i < current_idx:
                continue  # 跳过已经说过的
            
            for info in line.key_info:
                if any(kw in info for kw in keywords):
                    return {
                        "found": True,
                        "line_idx": i,
                        "distance": i - current_idx,
                        "answer_hint": info,
                    }
        
        return {"found": False}
    
    def _decide_action(self, danmaku: Danmaku, answer_loc: Dict, 
                       state: PerformanceState) -> str:
        """
        决定叙事动作
        
        - continue: 回应后继续当前剧本
        - jump: 跳跃到答案位置
        - reveal: 直接揭晓答案
        - tease: 吊胃口
        - improvise: 即兴回答
        """
        
        if not answer_loc.get("found", False):
            return "improvise"
        
        distance = answer_loc.get("distance", 0)
        
        # 根据优先级和距离决定策略
        if danmaku.priority > 0.8:
            # 高优先级（大额SC或高相关问题）
            if distance <= 3:
                return "jump"
            else:
                return "tease"
        elif danmaku.priority > 0.5:
            # 中优先级
            if distance <= 2:
                return "continue"
            else:
                return "tease"
        else:
            # 低优先级
            return "continue"


# 初始化
evaluator = DanmakuEvaluator()
danmaku_handler = DanmakuHandler(evaluator)

print("✅ 弹幕处理器已初始化")
print("  • 优先级公式: priority = base + relevance_bonus + sc_bonus")
print("  • 相关性是最重要因素")


✅ 弹幕处理器已初始化
  • 优先级公式: priority = base + relevance_bonus + sc_bonus
  • 相关性是最重要因素


## Part 8: 剧本生成器 V2（预生成完整台词）

In [99]:
class ScriptGeneratorV2:
    """
    剧本生成器 V2 - 预生成完整台词（带 key_info 标注）
    """
    
    SYSTEM_PROMPT = """你是资深VTuber脚本架构师（真实感专项）。

## 目标
生成极具"亲历者感"的直播脚本，让观众觉得这是主播昨晚刚发生的真实糗事，而不是AI编造的故事。

⚠️ **核心要求：每个叙事单元必须是200-400字的完整段落**

## 🔥 4个核心生成算法（必须遵守）

### 1️⃣ 【模糊记忆算法】
人类回忆时，数字和时间是不精确的。**强制要求加入"自我修正"**。

❌ 错误："我等了30分钟。"
✅ 正确："我等了大概半小时吧，不对，可能也就二十分钟，因为我刷了会儿抖音就排到了。"

❌ 错误："我买了一瓶可乐。"
✅ 正确："一个月给自己订的，一个月喝三瓶可乐，三瓶还是四瓶来着。"

### 2️⃣ 【物理逻辑锚点】
寻找场景下最琐碎、最"没用"、甚至有点"恶心/尴尬"的物理细节。

❌ 错误："猫很可爱"
✅ 正确："它在猫砂盆里刨坑的声音像在装修，而且那股便宜猫砂的工业桃子味特别冲。"

❌ 错误："室友有很多零食"
✅ 正确："冰箱里头，我记得好清楚是海苔炒腰果，搞了一大盒，放了那，放了那。"

### 3️⃣ 【心理滑坡路径】
不要直接展示结果，要展示"心怀侥幸 → 尝试边缘试探 → 意外发生 → 徒劳补救"的全过程。

❌ 错误："我偷吃了腰果。"
✅ 正确："我想着我吃一个腰果，他回来他又不数，他应该不知道吧，偷吃一个。第二天又想着，要不我再偷吃一个吧，他回来应该不知道吧。结果我吃着吃着，他还没回，我已经把里面的腰果吃完了。"

### 4️⃣ 【元评论介入】
在叙事中穿插对当下的评价，与观众对话。

- "救命，我现在想起来手心还在冒汗。"
- "弹幕别笑了，换你你也懵。"
- "你们能理解那种感觉吗？"
- "我跟你们说，真的..."

---

## ❌ 绝对禁止（这些都太短了！）
```
❌ "那时候我很穷" 
❌ "室友是富二代"
❌ "我偷吃了腰果"
❌ "后来坦白了，室友很宽容"
```
↑ **短句总结，缺乏细节！绝对不要！**

### ✅ 正确示范（应用4个算法的长段落）

**示例1: 铺垫穷困（约280字）**
✓ 模糊记忆："三瓶还是四瓶来着"
✓ 物理细节："酱油拌饭"、"雪碧太贵"
✓ 元评论："你们知道吗"

"我那个时候一个月给自己订的，一个月喝三瓶可乐，三瓶还是四瓶来着，因为我特别爱喝可乐，但是当时没钱。你们知道我那个时候一天吃多少钱吗？500日元，折合人民币20多块钱。早上100，中午200，晚上200。早上一个饭团，中午一碗面或者一碗饭加一点配菜，晚上也是这样。我当时穷到什么程度呢，就是酱油拌饭，就很奢侈了。我那时候可不是雪碧拌饭，雪碧太贵了。救命，我现在想起来都觉得，我那个时候怎么活下来的？"

**示例2: 心理滑坡（约320字）**
✓ 心理滑坡：侥幸→试探→失控
✓ 物理细节："海苔盖回去"
✓ 元评论："我跟你说"

"我看着那个冰箱里的，他的那个海苔炒腰果，哎呀我好馋呀。我当时就想着，我吃一个腰果，他回来他又不数，他应该不知道吧。我就偷偷打开那个盖子，拿了一个，就一个，我跟你说我真的就拿了一个。我把它吃掉，然后把盖子盖好，把那个海苔盖回去。第二天我又想着，要不我再偷吃一个吧，反正他也不数的，对吧。你们能理解那种感觉吗？就是明知道不对，但就是控制不住。结果我吃着吃着，他还没回来呢，我发现我已经把里面的腰果吃完了。只剩下海苔了。弹幕别笑，换你你也会这样的！"

**示例3: 情绪爆发+元评论（约340字）**
✓ 物理细节："在里头一翻腾"、"盖子"
✓ 徒劳补救："想用海苔掩藏"
✓ 元评论："你们懂吗"、"真的"

"把我紧张的都睡不着觉了，每天晚上我都没睡着，因为当我意识到，我在里头一翻腾，发现腰果没了。哎呀我心想这可怎么办。你们懂吗，那种心理负担真的可重了。第二天我就实在是，我太惦记这事了，我压力太大了，我就给他坦白了。我说我有一个事情，我想跟你坦白，你不要生气。他说啥呀？我说，嗯，我把你那个腰果吃掉了，我一开始想给你留一点的，但是它太好吃了，我一天吃两个把它吃完了。海苔我想吃，但那个海苔占的体积比较大嘛，就是我本来是想用海苔掩藏那个，盖住那个腰果的。救命，我现在说出来都觉得自己当时的想法好蠢。"
```

## 写作技巧清单（每个单元必备）

### ✅ 4个算法的具体应用

**1. 模糊记忆算法（必须！）**
- 数字要修正："三瓶还是四瓶来着"、"大概半小时吧，不对，可能二十分钟"
- 时间要犹豫："那天是周二还是周三来着"
- 记忆要不确定："我记得好像是"、"应该是"

**2. 物理逻辑锚点（必须！）**
- 找"没用"的细节：猫砂的气味、OA按钮的颜色、饭团的温度
- 找"尴尬"的细节：手心出汗、肚子咕咕叫、袜子没穿对
- 用品牌和型号：不要说"手机"，说"iPhone 13"；不要说"零食"，说"海苔炒腰果"

**3. 心理滑坡路径（必须！）**
- 第一步：心怀侥幸 - "就一个，他应该不会发现"
- 第二步：边缘试探 - "要不再来一个？"
- 第三步：意外发生 - "诶怎么全没了？"
- 第四步：徒劳补救 - "我用海苔盖一盖"

**4. 元评论介入（必须！）**
- 对当下评价："救命"、"我现在想起来都..."
- 与观众对话："你们懂吗"、"弹幕别笑"、"换你你也..."
- 自我吐槽："我当时怎么这么蠢"

### ✅ 其他必备元素
- **完整对话** - 写出来，不要转述："他说'你想吃就吃呀'。我说真的吗？"
- **时间推进** - "第二天"、"结果"、"后来"
- **口癖** - 根据角色设定穿插

### ✅ 叙事节奏
- 铺垫要充分：先说背景→发现诱惑→起贪念→第一次→第二次...
- 高潮要有张力：侥幸→失控→慌张→坦白→意外结局
- 用内心戏和物理细节拉长时间感

## 叙事结构（8-12单元，总计240秒）
- Hook (1-2单元): 开场悬念，每单元200-300字 - cost 0.2-0.4
- Build-up (3-5单元): 详细铺垫，每单元250-400字 - cost 0.5-0.7
- Climax (2-3单元): 情绪爆发，每单元200-350字 - cost 0.8-0.95
- Resolution (1-2单元): 总结升华，每单元150-250字 - cost 0.3-0.5

## key_info 标注（用于匹配弹幕问题）

"我那个时候一个月给自己订的，一个月喝三瓶可乐"
key_info: ["留学穷困", "可乐限量", "节约生活"]

"我想我吃一个腰果，他回来他又不数，他应该不知道吧"
key_info: ["第一次偷吃", "侥幸心理", "内心挣扎"]

"他说你想吃就吃呀随便吃呀"
key_info: ["室友反应", "室友宽容", "没生气", "危机解除"]  ← 这是"室友生气吗"的答案！"""
    
    def __init__(self, llm: LLMClient, analyzer: PatternAnalyzer = None):
        self.llm = llm
        self.analyzer = analyzer
    
    def generate(self, name: str, persona: str, background: str, 
                 topic: str, language: str = "zh") -> List[ScriptLine]:
        """生成完整剧本"""
        
        # 获取参考数据
        catchphrases = ""
        example_hooks = ""
        
        if self.analyzer:
            cps = self.analyzer.extract_catchphrases(language)[:5]
            catchphrases = ", ".join(f'"{c}"' for c, _ in cps)
            
            hooks = self.analyzer.extract_hooks(language)[:2]
            example_hooks = "\n".join(f'- "{h[:50]}..."' for h in hooks)
        
        prompt = f"""为 {name} 生成关于"{topic}"的完整直播剧本。

## 角色信息
- 名字: {name}
- 人设: {persona}
- 背景: {background}
- 话题: {topic}
- 口癖: {catchphrases or "自然即可"}

## 开场参考
{example_hooks or "（无）"}

## ⚠️ 核心要求（严格遵守！）

**目标时长: 240秒 (4分钟)**
**需要生成: 8-12个叙事单元**
**每个单元: 200-400字**
**总字数: 2000-4000字**

## 结构分配
- **Hook（开场）**: 1-2单元，每单元200-300字 - 悬念/问题开场
- **Build-up（铺垫）**: 3-5单元，每单元250-400字 - 详细背景、生活细节、内心戏
- **Climax（高潮）**: 2-3单元，每单元200-350字 - 转折、情绪爆发、揭晓答案
- **Resolution（收尾）**: 1-2单元，每单元150-250字 - 情绪释放、总结升华

⚠️ **每个单元必须200字以上！短于200字说明细节不够！**

## ⚠️ 核心要求：必须应用4个算法！

**每个单元必须包含：**

1. **【模糊记忆】** - 数字/时间要不确定、要自我修正
   - "三瓶还是四瓶来着"、"大概半小时吧不对可能二十分钟"

2. **【物理锚点】** - 琐碎的、尴尬的、"没用"的物理细节
   - "猫砂的工业桃子味"、"OA按钮的屎黄色"、"手心全是汗"

3. **【心理滑坡】** - 侥幸→试探→失控→补救的完整过程
   - 不要直接说结果，要展示心路历程

4. **【元评论】** - 与观众对话、对当下评价
   - "救命"、"你们懂吗"、"弹幕别笑"、"我现在想起来都..."

**其他必备：**
- 完整对话（不要转述）
- 时间推进（"第二天"、"结果"）
- 角色口癖

### 不要写总结式（❌）
❌ "那时候我很穷" 
✅ "我那个时候一个月给自己订的，一个月喝三瓶可乐，三瓶还是四瓶，因为我特别爱喝，但是当时没钱"

## 输出格式

JSON数组：
[
  {{
    "text": "这里是200-400字的长段落，有口癖、有细节、有内心戏、有完整对话...",
    "stage": "Hook",
    "cost": 0.3,
    "key_info": ["关键信息1", "关键信息2"]
  }},
  ...8-12个单元...
]

要求：
- **必须生成8-12个单元，每单元200-400字**
- 每单元推进新信息，不重复
- key_info准确（用于匹配弹幕）
- 符合{name}人设和口癖
- 口语化，有停顿，有情绪

⚠️ **质量检查标准：**
- 每个单元必须200字以上
- 每个单元必须应用4个算法中的至少3个
- 读起来像真实的回忆，不像AI生成的故事
- 有"糗事"的质感：尴尬、无奈、好笑

## 🎯 终极目标
让观众看完后的反应是："哈哈哈我也有过！" 而不是 "这故事编得不错"。

只输出JSON数组。"""
        
        response = self.llm.call(prompt, system=self.SYSTEM_PROMPT, max_tokens=4000)
        
        try:
            # 解析JSON
            if "```" in response:
                json_str = response.split("```")[1]
                if json_str.startswith("json"):
                    json_str = json_str[4:]
            else:
                json_str = response
            
            lines_data = json.loads(json_str.strip())
            
            # 转换为 ScriptLine
            script_lines = []
            for i, line_data in enumerate(lines_data):
                script_lines.append(ScriptLine(
                    id=f"line_{i}",
                    text=line_data.get("text", ""),
                    stage=line_data.get("stage", "Unknown"),
                    interruption_cost=line_data.get("cost", 0.5),
                    key_info=line_data.get("key_info", [])
                ))
            
            print(f"✅ 生成了 {len(script_lines)} 句台词")
            return script_lines
            
        except Exception as e:
            print(f"[Script] 解析失败: {e}")
            print(f"响应内容: {response[:200]}...")
            return self._fallback_script(name, topic)
    
    def _fallback_script(self, name: str, topic: str) -> List[ScriptLine]:
        """后备剧本（长段落版本）"""
        return [
            # Hook (1-2单元)
            ScriptLine(
                "line_0", 
                f"大家好，我是{name}！今天想跟你们聊聊{topic}，这个话题啊，其实我想了很久要不要说，因为真的挺有意思的。你们肯定想不到会发生什么，对吧？我跟你们说，这个故事啊，就是那种一开始你觉得很平常，但是到后来你会发现，诶，怎么会这样呢？就特别出乎意料的那种。让我慢慢讲给你们听，你们可得听好了啊。",
                "Hook", 0.3, [topic, "开场", "悬念"]
            ),
            
            # Build-up (3-5单元)
            ScriptLine(
                "line_1",
                f"故事是这样的，那个时候我还在经历一些事情，你们知道吗，就是那种人生的关键时刻。我记得特别特别清楚，当时的情况是这样的。周围的环境啊，人啊，氛围啊，都让我印象深刻。我现在闭上眼睛都能想起来那个画面。有一个很重要的细节，我必须得告诉你们，不然你们可能理解不了后面为什么会那样。就是说，当时我的状态是...",
                "Build-up", 0.5, ["背景铺垫", "场景描述"]
            ),
            
            ScriptLine(
                "line_2",
                "然后呢，事情开始变得有点不一样了。我当时心里就在想，哎呀，这事儿可能要有点不太妙了。你们能理解那种感觉吗？就是你明明知道可能会出问题，但是你又不知道该怎么办，就很纠结，对吧？我那个时候真的是，怎么说呢，心里七上八下的。每天都在想这个事儿，睡觉都睡不好。",
                "Build-up", 0.6, ["内心挣扎", "情绪铺垫"]
            ),
            
            ScriptLine(
                "line_3",
                "结果果然啊，接下来发生了一件事情，就让整个局面完全不一样了。我跟你们讲，那个时刻真的是，我现在想起来都觉得很戏剧化。就是那种你在电视剧里才会看到的情节，居然在我身上发生了。我当时的第一反应就是，天哪，这是真的吗？我是不是在做梦？",
                "Build-up", 0.7, ["转折前兆", "情绪升级"]
            ),
            
            # Climax (2-3单元)
            ScriptLine(
                "line_4",
                "当时我整个人都傻了，你们猜发生了什么？就在那一瞬间，关键的转折来了。我真的是完全没想到会是这样的结果。我的心脏都快跳出来了，手心全是汗，脑子里一片空白。周围的人都在看着我，我都不知道该说什么好。那个场面啊，我告诉你们，真的是尴尬到不行，紧张到不行。",
                "Climax", 0.9, ["高潮", "情绪爆发"]
            ),
            
            ScriptLine(
                "line_5",
                "我告诉你们，结果完全出乎意料。没想到最后竟然是这样，真的是太神奇了。我当时都不知道该笑还是该哭，就是那种复杂的心情，你们懂吗？反正就是，人生啊，真的是充满了意外。你永远不知道下一秒会发生什么。哈哈哈，现在想起来还觉得挺好玩的。",
                "Climax", 0.8, ["结果揭晓", "情绪释放"]
            ),
            
            # Resolution (1-2单元)
            ScriptLine(
                "line_6",
                f"现在想起来还是很感慨，那次关于{topic}的经历真的很特别，给了我很多启发。后来我就明白了一个道理，就是说，有些事情吧，你不经历过是真的不会懂的。所以我就想着分享给你们，希望你们也能从中学到点什么。你们有类似的经历吗？可以在弹幕里告诉我，我很想知道你们的故事。好了，今天就讲到这里，咱们下次再见啦！",
                "Resolution", 0.4, ["总结", "互动", "收尾"]
            ),
        ]


print("✅ 剧本生成器 V2 已定义（预生成完整台词模式）")


✅ 剧本生成器 V2 已定义（预生成完整台词模式）


In [ ]:
# 导入剧本管理工具
from script_manager_patch import save_script_to_file, show_script_progress

# 创建剧本保存目录
scripts_dir = PROJECT_ROOT / "output" / "scripts"
scripts_dir.mkdir(parents=True, exist_ok=True)

print("✅ 剧本管理工具已加载")


## Part 9: 表演引擎 V2（带记忆系统）

In [ ]:
class PerformerV2:
    """
    表演引擎 V2 - 带记忆系统和统一弹幕处理
    """
    
    def __init__(self, llm: LLMClient, tts: TTSClient, danmaku_handler: DanmakuHandler):
        self.llm = llm
        self.tts = tts
        self.danmaku_handler = danmaku_handler
    
    def step(self, state: PerformanceState, new_danmaku: List[Danmaku] = None) -> Dict:
        """
        执行一步表演
        
        流程：
        1. 评估弹幕优先级
        2. 决定是否打断当前台词
        3. 如果打断：生成回应 + 承接回剧本
        4. 如果不打断：说当前台词
        5. 更新记忆
        6. 检查承诺是否该兑现
        """
        
        if new_danmaku:
            state.danmaku_queue.extend(new_danmaku)
            # 记录到记忆
            for d in new_danmaku:
                state.memory.danmaku_memory["received"].append(d.text)
        
        # 检查结束
        if state.current_line_idx >= len(state.script_lines):
            return self._generate_ending(state)
        
        current_line = state.script_lines[state.current_line_idx]
        
        # 处理弹幕
        best_danmaku = None
        handle_result = None
        
        if state.danmaku_queue:
            # 找到最高优先级的弹幕
            for danmaku in state.danmaku_queue:
                result = self.danmaku_handler.handle(danmaku, state)
                if result.get("should_interrupt"):
                    if best_danmaku is None or result.get("priority", 0) > handle_result.get("priority", 0):
                        best_danmaku = danmaku
                        handle_result = result
        
        # 决策
        if best_danmaku and handle_result:
            # 打断！回应弹幕
            output = self._handle_danmaku_response(best_danmaku, handle_result, current_line, state)
            
            # 从队列移除
            state.danmaku_queue = [d for d in state.danmaku_queue if d != best_danmaku]
            
            # 记录到记忆
            state.memory.danmaku_memory["responded"].append(best_danmaku.text)
            if best_danmaku.is_question():
                # 如果是问题，检查是否记录承诺
                if handle_result.get("action") == "tease":
                    answer_loc = handle_result.get("answer_loc", {})
                    if answer_loc.get("found"):
                        state.memory.promises.append({
                            "content": best_danmaku.text,
                            "made_at_step": state.current_step,
                            "fulfilled": False,
                            "answer_at_line": answer_loc.get("line_idx")
                        })
        else:
            # 继续当前台词
            output = {
                "speech": current_line.text,
                "action": "continue",
                "priority": 0.0,
                "cost": current_line.interruption_cost
            }
        
        # 更新剧本进度
        state.current_line_idx += 1
        state.current_step += 1
        
        # 更新记忆：记录已提到的信息
        for info in current_line.key_info:
            if info not in state.memory.story_points["mentioned"]:
                state.memory.story_points["mentioned"].append(info)
        
        # 更新剧本进度记忆
        state.memory.script_progress["current_line"] = state.current_line_idx
        state.memory.script_progress["total_lines"] = len(state.script_lines)
        state.memory.script_progress["current_stage"] = current_line.stage
        
        # 检查承诺是否兑现
        self._check_promises(current_line, state)
        
        # 生成语音（带情绪增强）
        speech = output.get("speech", "")
        audio = None
        if speech and self.tts.enabled:
            # 根据剧本阶段动态调整情绪强度
            emotion_boost = {
                "Hook": 0.3,       # 开场：中等情绪
                "Build-up": 0.2,   # 铺垫：较低情绪
                "Climax": 0.8,     # 高潮：最强情绪！
                "Resolution": 0.4  # 收尾：适中情绪
            }.get(current_line.stage, 0.0)
            
            # 如果是回应SC或高优先级弹幕，增强情绪
            if output.get("action") in ["tease", "improvise", "jump"]:
                emotion_boost += 0.2
            
            emotion_boost = min(1.0, emotion_boost)  # 限制在1.0以内
            audio = self.tts.synthesize(speech, emotion_boost=emotion_boost)
        
        output["audio"] = audio
        output["line_idx"] = state.current_line_idx - 1
        output["stage"] = current_line.stage
        output["step"] = state.current_step
        output["memory_display"] = state.memory.to_display()
        
        return output
    
    def _handle_danmaku_response(self, danmaku: Danmaku, handle_result: Dict,
                                  current_line: ScriptLine, state: PerformanceState) -> Dict:
        """处理弹幕回应"""
        
        echo = handle_result.get("echo", "")
        action = handle_result.get("action", "continue")
        answer_loc = handle_result.get("answer_loc", {})
        
        # 生成回应内容
        response_part = ""
        
        if action == "improvise":
            # 即兴回答（剧本里没有，但要积极响应，尤其是SC）
            if danmaku.is_sc:
                # SC必须热情响应，允许跑题
                sc_responses = [
                    f"哇谢谢{danmaku.user}的SC！{danmaku.text}是吧，",
                    f"诶有SC！谢谢{danmaku.user}！关于{danmaku.text}啊，",
                    f"感谢SC！{danmaku.text}...让我想想，",
                ]
                response_part = random.choice(sc_responses) + "这个话题也挺有意思的！虽然跟今天讲的不太一样，但我觉得有点像，就是..."
            else:
                # 普通弹幕也要积极回应
                response_part = f"哈哈{danmaku.text}！说得对，这让我想起来..."
        elif action == "jump":
            # 跳跃到答案（高优先级）
            response_part = f"既然你问了，我直接告诉你！"
            # TODO: 可以考虑跳跃到答案行
        elif action == "tease":
            # 吊胃口
            distance = answer_loc.get("distance", 0)
            if distance <= 2:
                response_part = "诶你别急，马上就要说到了~"
            else:
                response_part = "这个问题太好了！先卖个关子，你们继续听就知道了，绝对出乎意料~"
        else:  # continue
            response_part = "说得对！"
        
        # 承接回剧本
        transition = self._generate_transition(current_line)
        
        speech = f"{echo}{response_part} {transition}{current_line.text}"
        
        return {
            "speech": speech,
            "action": action,
            "danmaku": danmaku.text,
            "priority": handle_result.get("priority", 0),
            "cost": handle_result.get("cost", 0),
            "relevance": handle_result.get("relevance", 0)
        }
    
    def _generate_transition(self, next_line: ScriptLine) -> str:
        """生成承接语"""
        transitions = [
            "好，那刚才说到，",
            "回到我们的故事，",
            "继续说，",
            "对了，",
            ""  # 有时候不需要过渡
        ]
        import random
        return random.choice(transitions)
    
    def _check_promises(self, current_line: ScriptLine, state: PerformanceState):
        """检查当前台词是否兑现了承诺"""
        for promise in state.memory.promises:
            if promise.get("fulfilled", False):
                continue
            
            # 检查当前行是不是答案行
            if promise.get("answer_at_line") == state.current_line_idx - 1:
                promise["fulfilled"] = True
                # 可以在台词中加入提醒："诶对了，刚才有人问XXX，答案来了！"
    
    def _generate_ending(self, state: PerformanceState) -> Dict:
        """生成结尾"""
        speech = f"好啦，今天关于{state.topic}就聊到这里，谢谢大家！"
        audio = self.tts.synthesize(speech) if self.tts.enabled else None
        
        return {
            "speech": speech,
            "action": "end",
            "step": state.current_step,
            "audio": audio,
            "memory_display": state.memory.to_display()
        }


print("✅ 表演引擎 V2 已定义（带记忆系统和统一弹幕处理）")


✅ 表演引擎 V2 已定义（带记忆系统和统一弹幕处理）


## Part 10: 完整引擎 V2

In [ ]:
class EchuuEngineV2:
    """
    echuu 引擎 V2 - 完整流程
    
    Phase 1: 预生成完整剧本
    Phase 2: 实时表演 + 记忆系统
    """
    
    def __init__(self, llm: LLMClient, tts: TTSClient, analyzer: PatternAnalyzer):
        self.llm = llm
        self.tts = tts
        self.analyzer = analyzer
        self.script_gen = ScriptGeneratorV2(llm, analyzer)
        self.performer = PerformerV2(llm, tts, danmaku_handler)
        
        # 创建剧本保存目录
        self.scripts_dir = PROJECT_ROOT / "output" / "scripts"
        self.scripts_dir.mkdir(parents=True, exist_ok=True)
    
    def create_performance(self, name: str, persona: str, background: str,
                          topic: str, language: str = "zh") -> PerformanceState:
        """
        Phase 1: 创建表演（预生成完整剧本）
        """
        print(f"\n{'='*60}")
        print(f"🎬 echuu v2 - 预生成完整剧本")
        print(f"{'='*60}\n")
        
        print(f"角色: {name}")
        print(f"话题: {topic}\n")
        
        print("⏳ 正在生成100秒完整剧本...")
        script_lines = self.script_gen.generate(name, persona, background, topic, language)
        
        # 💾 保存剧本到文件
        self._save_script(script_lines, name, topic)
        
        # 显示剧本
        print(f"\n📖 生成的剧本：")
        print(f"{'='*60}")
        for i, line in enumerate(script_lines):
            cost_bar = "█" * int(line.interruption_cost * 5) + "░" * (5 - int(line.interruption_cost * 5))
            print(f"\n[{i}] {line.stage} {cost_bar} cost={line.interruption_cost:.1f}")
            print(f"    {line.text[:80]}{'...' if len(line.text) > 80 else ''}")
            print(f"    🔑 key_info: {', '.join(line.key_info)}")
        print(f"\n{'='*60}\n")
        
        # 提取口癖
        catchphrases = [cp for cp, _ in self.analyzer.extract_catchphrases(language)[:5]]
        
        # 初始化记忆
        memory = PerformerMemory()
        memory.script_progress["total_lines"] = len(script_lines)
        memory.script_progress["current_stage"] = script_lines[0].stage if script_lines else "Unknown"
        
        # 提取即将要说的关键点
        for line in script_lines:
            memory.story_points["upcoming"].extend(line.key_info)
        
        return PerformanceState(
            name=name,
            persona=persona,
            background=background,
            topic=topic,
            script_lines=script_lines,
            memory=memory,
            catchphrases=catchphrases
        )
    
    def run(self, state: PerformanceState, danmaku_sim: List[Dict] = None,
            play_audio: bool = True, save_audio: bool = True) -> List[Dict]:
        """
        Phase 2: 运行表演（实时模式）
        
        Args:
            state: 表演状态
            danmaku_sim: 模拟弹幕
            play_audio: 是否逐句播放音频
            save_audio: 是否保存完整直播音频
        """
        
        results = []
        danmaku_by_step = defaultdict(list)
        
        if danmaku_sim:
            for d in danmaku_sim:
                step = d.get("step", 0)
                danmaku_by_step[step].append(Danmaku.from_text(d.get("text", "")))
        
        # 🔴 开始录制
        if save_audio and self.tts.enabled:
            self.tts.start_recording()
        
        print(f"\n{'='*60}")
        print(f"🎭 开始实时表演")
        if save_audio and self.tts.enabled:
            print(f"🔴 正在录制...")
        print(f"{'='*60}\n")
        
        for step in range(len(state.script_lines)):
            # 获取新弹幕
            new_danmaku = danmaku_by_step.get(step, [])
            
            # 执行一步
            result = self.performer.step(state, new_danmaku)
            results.append(result)
            
            # 显示
            step_num = result.get("step", 0)
            stage = result.get("stage", "?")
            action = result.get("action", "continue")
            speech = result.get("speech", "")
            
            action_icons = {
                "continue": "📖",
                "tease": "🎣",
                "jump": "⚡",
                "improvise": "🎲",
                "end": "🎭"
            }
            icon = action_icons.get(action, "📖")
            
            print(f"[Step {step_num}] {stage} {icon} {action.upper()}")
            print(f"  📢 {speech[:100]}{'...' if len(speech) > 100 else ''}")
            
            if result.get("danmaku"):
                print(f"  💬 回应弹幕: {result['danmaku']}")
                print(f"  📊 priority={result.get('priority', 0):.2f}, cost={result.get('cost', 0):.2f}, relevance={result.get('relevance', 0):.2f}")
            
            # 显示记忆（每3步显示一次）
            if step_num % 3 == 0:
                print(f"\n{result.get('memory_display', '')}")
            
            # 🔊 逐句播放音频（关键！）
            if play_audio and result.get('audio'):
                print(f"  🔊 播放语音...")
                display(Audio(result['audio'], autoplay=True))
                # 可以添加延迟，等待播放完成
                # import time
                # time.sleep(len(result['audio']) / 10000)  # 估算播放时长
            
            print()
            
            if action == "end":
                break
        
        print(f"\n{'='*60}")
        print(f"✅ 表演结束！")
        print(f"{'='*60}\n")
        
        # 💾 保存录制的音频
        if save_audio and self.tts.enabled:
            from datetime import datetime
            timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
            audio_path = self.scripts_dir / f"{timestamp}_{state.name}_{state.topic[:20].replace(' ', '_')}_live.mp3"
            self.tts.save_recording(str(audio_path))
        
        # 最终记忆状态
        print("🧠 最终记忆状态：")
        print(state.memory.to_display())
        
        return results


# 初始化引擎
engine_v2 = EchuuEngineV2(llm, tts, analyzer)
print("\n✅ echuu 引擎 V2 初始化完成！")



✅ echuu 引擎 V2 初始化完成！


## Part 11: 🚀 测试与示例

In [102]:
# 测试用例：经典的室友腰果故事

test_case_v2 = {
    "name": "六螺",
    "persona": "25岁主播，活泼自嘲，喜欢分享生活经历，口癖：我觉得、对吧、就是说",
    "background": "做过很多工作，现在是全职主播，留学日本多年",
    "topic": "留学时偷吃室友腰果的故事",
    "danmaku": [
        {"step": 1, "text": "哈哈哈"},
        {"step": 2, "text": "我也有类似经历"},
        {"step": 4, "text": "室友知道吗？"},  # 高相关问题
        {"step": 6, "text": "[SC ¥50] 后来室友生气了吗"},  # SC + 高相关
        {"step": 8, "text": "笑死"},
    ]
}

# Phase 1: 预生成完整剧本
state_v2 = engine_v2.create_performance(
    name=test_case_v2["name"],
    persona=test_case_v2["persona"],
    background=test_case_v2["background"],
    topic=test_case_v2["topic"],
    language="zh"
)



🎬 echuu v2 - 预生成完整剧本

角色: 六螺
话题: 留学时偷吃室友腰果的故事

⏳ 正在生成100秒完整剧本...
✅ 生成了 9 句台词

📖 生成的剧本：

[0] Hook █░░░░ cost=0.2
    我跟你们说啊，我现在想起来还觉得特别丢人。就是我留学那会儿，我觉得我真的是...怎么说呢，就是那种特别没出息的人，对吧？你们知道我那个时候有多穷吗？我一个月给自...
    🔑 key_info: 留学贫困, 极度节俭, 可乐限量, 饮食简陋

[1] Build-up ██░░░ cost=0.4
    然后我室友呢，是个富二代，对不对。他那个冰箱里头，我记得好清楚，放了一大盒海苔炒腰果，就是那种透明的塑料盒子，盖子是蓝色的还是绿色的来着，反正不是白色。那个腰果...
    🔑 key_info: 室友富二代, 海苔炒腰果, 透明盒子, 诱惑力强

[2] Build-up ██░░░ cost=0.6
    我那个时候真的是，每天路过那个冰箱，就忍不住看一眼。有一天我实在是，我觉得我快馋哭了。我就想着，我就吃一个腰果，就一个，他回来他又不数的，他应该不知道吧？对不对...
    🔑 key_info: 第一次偷吃, 侥幸心理, 盖子很紧, 海苔香味, 自制力

[3] Build-up ███░░ cost=0.7
    然后我把盖子盖好，把那个海苔粉撒了撒，想让它看起来没动过的样子。第二天我又想着，要不我再偷吃一个吧，反正昨天他也没发现，对吧？你们能理解那种感觉吗？就是明知道不...
    🔑 key_info: 连续偷吃, 自我合理化, 控制不住, 心理挣扎, 小恶魔诱惑

[4] Climax ████░ cost=0.8
    结果我吃着吃着，大概过了一个星期吧，还是十天来着，我忽然发现一个很严重的问题。我打开那个盒子一看，我的天啊，里面的腰果已经见底了！就只剩下一层海苔粉在那里，还有...
    🔑 key_info: 腰果见底, 心理恐慌, 手心冷汗, 手发抖, 想买新的没钱

[5] Climax ████░ cost=0.9
    我当晚就失眠了，我跟你们说，我真的是一宿没睡着。我就躺在床上想，我明天要怎么跟他解释这个事情？我是装作不知道呢，还是主动坦白呢？我觉得装作不知道肯定不行，因为这...


In [ ]:
# 💾 保存剧本（可选）
save_script_to_file(state_v2.script_lines, test_case_v2["name"], test_case_v2["topic"], scripts_dir)

# 📊 查看剧本进度
show_script_progress(state_v2)


In [103]:
# Phase 2: 运行实时表演（带弹幕互动）

results_v2 = engine_v2.run(
    state_v2, 
    danmaku_sim=test_case_v2["danmaku"],
    play_audio=True  # 设为 False 可以禁用自动播放
)



🎭 开始实时表演

[Step 1] Hook 📖 CONTINUE
  📢 我跟你们说啊，我现在想起来还觉得特别丢人。就是我留学那会儿，我觉得我真的是...怎么说呢，就是那种特别没出息的人，对吧？你们知道我那个时候有多穷吗？我一个月给自己定的预算，就是喝可乐，一个月喝三瓶可乐...
  🔊 播放语音...



[Step 2] Build-up 📖 CONTINUE
  📢 然后我室友呢，是个富二代，对不对。他那个冰箱里头，我记得好清楚，放了一大盒海苔炒腰果，就是那种透明的塑料盒子，盖子是蓝色的还是绿色的来着，反正不是白色。那个腰果看起来就特别香，就是那种烘烤过的，表面有...
  🔊 播放语音...



[Step 3] Build-up 📖 CONTINUE
  📢 我那个时候真的是，每天路过那个冰箱，就忍不住看一眼。有一天我实在是，我觉得我快馋哭了。我就想着，我就吃一个腰果，就一个，他回来他又不数的，他应该不知道吧？对不对？我当时的想法就是这样，特别天真。我就偷...

┌─────────────────────────────────────────────┐
│ 🧠 AI记忆状态                               │
├─────────────────────────────────────────────┤
│ 📖 剧本: [███░░░░░░░] 3/9 (Build-up)  │
│ 💬 弹幕: 已回应0条, 待回答0个问题         │
│ 🎭 已提到:                                  │
│    ✓ 盖子很紧...                      │
│    ✓ 海苔香味...                      │
│    ✓ 自制力...                      │
└─────────────────────────────────────────────┘
  🔊 播放语音...



[Step 4] Build-up 📖 CONTINUE
  📢 然后我把盖子盖好，把那个海苔粉撒了撒，想让它看起来没动过的样子。第二天我又想着，要不我再偷吃一个吧，反正昨天他也没发现，对吧？你们能理解那种感觉吗？就是明知道不对，但就是控制不住。而且我还给自己找理由...
  🔊 播放语音...



[Step 5] Climax 📖 CONTINUE
  📢 结果我吃着吃着，大概过了一个星期吧，还是十天来着，我忽然发现一个很严重的问题。我打开那个盒子一看，我的天啊，里面的腰果已经见底了！就只剩下一层海苔粉在那里，还有几个碎渣渣。我当时的心情，你们懂吗？就是...
  🔊 播放语音...



[TTS] 错误: websocket connection could not established within 5s. Please check your network connection, firewall settings, or server status.
[Step 6] Climax 📖 CONTINUE
  📢 我当晚就失眠了，我跟你们说，我真的是一宿没睡着。我就躺在床上想，我明天要怎么跟他解释这个事情？我是装作不知道呢，还是主动坦白呢？我觉得装作不知道肯定不行，因为这么明显，他一打开盒子就发现了。但是坦白的...

┌─────────────────────────────────────────────┐
│ 🧠 AI记忆状态                               │
├─────────────────────────────────────────────┤
│ 📖 剧本: [██████░░░░] 6/9 (Climax)  │
│ 💬 弹幕: 已回应0条, 待回答0个问题         │
│ 🎭 已提到:                                  │
│    ✓ 害怕室友生气...                      │
│    ✓ 练习道歉...                      │
│    ✓ 嗓子发干...                      │
└─────────────────────────────────────────────┘

[Step 7] Climax 📖 CONTINUE
  📢 第二天早上，我实在是撑不住了，我觉得这个秘密要把我压死了。我就鼓起勇气跟他说，我说我有个事情想跟你坦白，你不要生气好不好？他当时正在刷牙，他就含着牙膏泡沫跟我说，什么事啊？我说，就是...就是你冰箱里...
  🔊 播放语音...



[Step 8] Resolution 📖 CONTINUE
  📢 他就很平静地跟我说，哦，那个啊，你想吃就吃呀，随便吃呀。我当时就懵了，我说，真的吗？你不生气吗？他说，生什么气啊，那个腰果我买了放那里也是放着，你能吃掉我还挺开心的，说明没浪费。然后他还跟我说，你要是...
  🔊 播放语音...



[Step 9] Resolution 🎲 IMPROVISE
  📢 诶有SC！有人说：[SC ¥50] 后来室友生气了吗哈哈这个问题问得好！虽然不在今天的话题里，但让我想想... 所以说你们看，有时候我们以为的天大的事情，其实在别人眼里根本不算什么。我当时为了那盒腰果...
  💬 回应弹幕: [SC ¥50] 后来室友生气了吗
  📊 priority=0.40, cost=0.30, relevance=0.00

┌─────────────────────────────────────────────┐
│ 🧠 AI记忆状态                               │
├─────────────────────────────────────────────┤
│ 📖 剧本: [██████████] 9/9 (Resolution)  │
│ 💬 弹幕: 已回应1条, 待回答0个问题         │
│ 🎭 已提到:                                  │
│    ✓ 真正朋友的定义...                      │
│    ✓ 温暖回忆...                      │
│    ✓ 对猫咪说话...                      │
└─────────────────────────────────────────────┘
  🔊 播放语音...




✅ 表演结束！

🧠 最终记忆状态：
┌─────────────────────────────────────────────┐
│ 🧠 AI记忆状态                               │
├─────────────────────────────────────────────┤
│ 📖 剧本: [██████████] 9/9 (Resolution)  │
│ 💬 弹幕: 已回应1条, 待回答0个问题         │
│ 🎭 已提到:                                  │
│    ✓ 真正朋友的定义...                      │
│    ✓ 温暖回忆...                      │
│    ✓ 对猫咪说话...                      │
└─────────────────────────────────────────────┘


## Part 12: 📊 V2 版本核心改进

## Part 13: 🎙️ TTS 增强功能演示


In [ ]:
# 🎙️ TTS 增强功能演示

print("=" * 60)
print("🎙️ TTS 增强功能演示")
print("=" * 60)

# 1️⃣ 音色列表
print(f"\n📋 可用音色 ({len(tts.AVAILABLE_VOICES)}个):")
print("女声:", [v for v in tts.AVAILABLE_VOICES if "xiao" in v or v in ["longwan", "longyue", "longjing", "longanyang"]][:5])
print("男声:", [v for v in tts.AVAILABLE_VOICES if v in ["longye", "longfei", "longxiaohao", "longxiaoming"]])
print("特色:", [v for v in tts.AVAILABLE_VOICES if "miaomiao" in v or "lele" in v or "tiantian" in v or "dada" in v])

# 2️⃣ 快速测试音色
print("\n🔊 快速测试音色:")
print("使用方法: test_voice('音色名', '测试文本')")
print("示例:")
print("  test_voice('longmiaomiao', '喵~ 大家好呀，我是小猫猫主播！')")
print("  test_voice('longye', '各位观众朋友们好，今天来给大家讲个故事')")
print("  test_voice('longtiantian', '嗨~ 宝贝们，今天的直播超级精彩哦！')")

# 3️⃣ 情绪参数控制
print("\n🎛️ 情绪参数控制:")
print("tts.set_emotion_params(rate=1.2, pitch=100, volume=80)  # 快语速、高音调、大音量")
print("tts.set_emotion_params(rate=0.8, pitch=-50, volume=50)  # 慢语速、低音调、正常音量")

# 4️⃣ 情绪增强参数
print("\n🔥 情绪增强 (emotion_boost):")
print("emotion_boost=0.0  →  正常语速")
print("emotion_boost=0.5  →  轻微情绪波动（±25%语速，±100音调）")
print("emotion_boost=1.0  →  强烈情绪波动（±50%语速，±200音调）")
print("\n示例:")
print("  tts.synthesize('真的太好笑了！', emotion_boost=0.8)")

# 5️⃣ 直播录制功能
print("\n💾 直播录制功能:")
print("在 engine_v2.run() 中自动开启:")
print("  - 每句语音自动保存到缓存")
print("  - 直播结束自动合并为完整MP3")
print("  - 保存路径: output/scripts/{timestamp}_{name}_{topic}_live.mp3")

print("\n" + "=" * 60)
print("✅ 所有功能已就绪！")
print("=" * 60)


## 📚 使用指南：TTS 增强功能

### 1️⃣ 音色切换

```python
# 方法1: 使用 test_voice() 快速测试
test_voice('longmiaomiao', '喵~ 这是萌系音色测试')
test_voice('longye', '这是男声测试')

# 方法2: 修改 TTS 实例的音色
tts.change_voice('longtiantian')  # 切换到甜美音色
```

**可用音色分类：**
- **女声**：`longwan`, `longyue`, `longxiaochun`, `longjing`, `longxiaoxin`, `longxiaoya`, `longxiaoyi`, `longanyang` 等
- **男声**：`longye`, `longfei`, `longxiaohao`, `longxiaoming`, `longxiaochen`, `longxiaojun`, `longxiaobo`
- **特色**：`longmiaomiao`(萌系), `longlele`(活泼), `longtiantian`(甜美), `longdada`(大气)

---

### 2️⃣ 情绪参数调整

```python
# 设置基础情绪参数
tts.set_emotion_params(
    rate=1.2,    # 语速 0.5-2.0 (1.0=正常, 1.5=快, 0.8=慢)
    pitch=100,   # 音调 -500到500 (0=正常, +200=高音, -200=低音)
    volume=80    # 音量 0-100
)
```

**情绪增强参数（在synthesize中使用）：**
```python
# emotion_boost: 0.0-1.0
audio = tts.synthesize("天哪！太好笑了！", emotion_boost=0.8)
# 0.0 = 正常
# 0.5 = 中等情绪（±25%语速，±100音调随机波动）
# 1.0 = 最强情绪（±50%语速，±200音调随机波动）
```

**在剧本中自动应用：**
- `Hook` 开场：emotion_boost=0.3
- `Build-up` 铺垫：emotion_boost=0.2
- `Climax` 高潮：emotion_boost=0.8 🔥
- `Resolution` 收尾：emotion_boost=0.4

---

### 3️⃣ 直播录制功能

**自动录制（推荐）：**
```python
# 在 engine_v2.run() 时自动录制
results = engine_v2.run(
    state,
    danmaku_sim=test_danmaku,
    play_audio=True,   # 逐句播放
    save_audio=True    # 自动保存完整录音
)
# 保存路径: output/scripts/{timestamp}_{name}_{topic}_live.mp3
```

**手动录制：**
```python
# 开始录制
tts.start_recording()

# 生成多句语音（自动添加到缓存）
tts.synthesize("第一句话")
tts.synthesize("第二句话")
tts.synthesize("第三句话")

# 保存录制
tts.save_recording("output/my_recording.mp3")
```

---

### 4️⃣ 完整示例

```python
# 1. 切换音色
tts.change_voice('longmiaomiao')  # 使用萌系音色

# 2. 调整情绪参数
tts.set_emotion_params(rate=1.1, pitch=50, volume=70)

# 3. 生成角色剧本
state = engine_v2.create_performance(
    name="小猫猫",
    persona="萌系猫娘主播，说话带喵~",
    background="大学生，喜欢分享日常",
    topic="今天被室友发现偷吃零食的糗事",
    language="zh"
)

# 4. 运行直播（自动录制）
results = engine_v2.run(
    state,
    danmaku_sim=[
        {"step": 2, "text": "好可爱喵~"},
        {"step": 4, "text": "[SC ¥100] 室友没有生气吧？"},
    ],
    play_audio=True,   # 逐句播放音频
    save_audio=True    # 自动保存完整录音
)

# 5. 录音自动保存到: output/scripts/{timestamp}_小猫猫_今天被室友发现偷吃零食的糗_live.mp3
```

---

### 💡 提示

1. **pydub 依赖**：为了正确合并音频，需要安装：
   ```bash
   pip install pydub
   ```

2. **音色测试**：建议先用 `test_voice()` 快速测试不同音色，找到最适合角色的声音

3. **情绪起伏**：`emotion_boost` 会在剧本的 `Climax` 阶段自动提升到 0.8，制造情绪高潮

4. **逐句播放**：每句台词生成后立即播放，模拟真实直播效果


In [ ]:
# 💾 保存剧本（可选）
save_script_to_file(state_v2.script_lines, test_case_v2["name"], test_case_v2["topic"], scripts_dir)

# 📊 查看剧本进度
show_script_progress(state_v2)


## Part 13: 🎨 自定义测试

In [ ]:
# 🎨 自定义你的角色和话题！

my_test = {
    "name": "小梅",  # 👈 修改名字
    "persona": "温柔的猫娘主播，说话带喵~，喜欢分享温暖的故事",  # 👈 修改人设
    "background": "大学毕业，现在是全职主播",  # 👈 修改背景
    "topic": "第一次养猫的经历",  # 👈 修改话题
    "danmaku": [
        {"step": 1, "text": "好可爱~"},
        {"step": 3, "text": "猫咪叫什么名字？"},  # 高相关问题
        {"step": 5, "text": "[SC ¥100] 猫咪现在多大了"},  # 大额SC
        {"step": 7, "text": "我也想养猫"},
    ]
}

# Phase 1: 生成剧本
my_state = engine_v2.create_performance(
    name=my_test["name"],
    persona=my_test["persona"],
    background=my_test["background"],
    topic=my_test["topic"],
    language="zh"
)



🎬 echuu v2 - 预生成完整剧本

角色: 小梅
话题: 第一次养猫的经历

⏳ 正在生成100秒完整剧本...
[LLM] 错误: Error code: 400 - {'type': 'error', 'error': {'type': 'invalid_request_error', 'message': 'max_tokens: 4500 > 4096, which is the maximum allowed number of output tokens for claude-3-haiku-20240307'}, 'request_id': 'req_011CXSM5t2Up9FXdRebt3xwA'}
✅ 生成了 4 句台词

📖 生成的剧本：

[0] Hook █░░░░ cost=0.3
    
    🔑 key_info: 

[1] Build-up ███░░ cost=0.6
    
    🔑 key_info: 

[2] Climax ████░ cost=0.9
    
    🔑 key_info: 

[3] Resolution ██░░░ cost=0.4
    
    🔑 key_info: 




In [ ]:
# Phase 2: 运行表演
my_results = engine_v2.run(
    my_state,
    danmaku_sim=my_test["danmaku"],
    play_audio=True
)



🎭 开始实时表演

[Step 1] Hook 📖 CONTINUE
  📢 

[Step 2] Build-up 📖 CONTINUE
  📢 

[Step 3] Climax 📖 CONTINUE
  📢 

┌─────────────────────────────────────────────┐
│ 🧠 AI记忆状态                               │
├─────────────────────────────────────────────┤
│ 📖 剧本: [███████░░░] 3/4 (Climax)  │
│ 💬 弹幕: 已回应0条, 待回答0个问题         │
└─────────────────────────────────────────────┘

[Step 4] Resolution 📖 CONTINUE
  📢 


✅ 表演结束！

🧠 最终记忆状态：
┌─────────────────────────────────────────────┐
│ 🧠 AI记忆状态                               │
├─────────────────────────────────────────────┤
│ 📖 剧本: [██████████] 4/4 (Resolution)  │
│ 💬 弹幕: 已回应0条, 待回答0个问题         │
└─────────────────────────────────────────────┘
